# **Change Data Capture with Azure SQL Database**

Change data capture (CDC) records insert, update, and delete activity that applies to a table. This makes the details of the changes available in an easily consumed relational format.

https://docs.microsoft.com/en-us/sql/relational-databases/track-changes/about-change-data-capture-sql-server

## Enable CDC

In [11]:
-- 01. Create Table
DROP TABLE IF EXISTS dbo.Customer;
CREATE TABLE Customer
(
    CustomerID INT PRIMARY KEY,
    CustomerAddress VARCHAR(255)
);

Commands completed successfully.

Total execution time: 00:00:00.085

In [12]:
-- 02. Enable change data capture for the current database
sys.sp_cdc_enable_db

Commands completed successfully.

Total execution time: 00:00:00.263

In [13]:
-- 03. Enables change data capture for the specified source table in the current database
sys.sp_cdc_enable_table 
    @source_schema = N'dbo',
    @source_name   = N'Customer',
    @role_name     = NULL,
    @supports_net_changes = 1  

Commands completed successfully.

Total execution time: 00:00:00.496

In [14]:
-- 04. As we have yet to trigger a DELETE/INSERT/UPDATE, the change table is initially empty
SELECT * FROM cdc.dbo_Customer_CT

(0 rows affected)

Total execution time: 00:00:00.085

__$start_lsn __$end_lsn __$seqval __$operation __$update_mask CustomerID CustomerAddress __$command_id

## Track Changes

In [15]:
-- 05. Populate the Customer table (INSERT)
INSERT INTO dbo.Customer
    (CustomerID, CustomerAddress)
VALUES
    (1, '82 Margate Drive, Sheffield, S4 8FQ'),
    (2, '135 High Barns, Ely, CB7 4RH'),
    (3, '39 Queen Annes Drive, Bedale, DL8 2EL');
SELECT * FROM dbo.Customer;

(3 rows affected)

(3 rows affected)

Total execution time: 00:00:00.096

CustomerID CustomerAddress 1 82 Margate Drive, Sheffield, S4 8FQ 2 135 High Barns, Ely, CB7 4RH 3 39 Queen Annes Drive, Bedale, DL8 2EL

In [17]:
-- 06. The change table returns three rows in total, one row for each INSERT. 
-- NOTE: The __$operation column identifies the DML operation associated with the change. 1 = delete, 2 = insert, 3 = update (old values), 4 = update (new values).
-- NOTE: There will be some latency between a transaction log being commited on a source table and the last captured transaction being committed on the change table.
-- NOTE: If the records are not immediately available, run cell again.
SELECT * FROM cdc.dbo_Customer_CT

(3 rows affected)

Total execution time: 00:00:00.095

__$start_lsn __$end_lsn __$seqval __$operation __$update_mask CustomerID CustomerAddress __$command_id 0x0000004200001BE800CD NULL 0x0000004200001BE800CA 2 0x03 1 82 Margate Drive, Sheffield, S4 8FQ 1 0x0000004200001BE800CD NULL 0x0000004200001BE800CB 2 0x03 2 135 High Barns, Ely, CB7 4RH 2 0x0000004200001BE800CD NULL 0x0000004200001BE800CC 2 0x03 3 39 Queen Annes Drive, Bedale, DL8 2EL 3

In [18]:
-- 07. Remove a row from the Customer table (DELETE)
DELETE FROM dbo.Customer WHERE CustomerID = 2;
SELECT * FROM dbo.Customer;

(1 row affected)

(2 rows affected)

Total execution time: 00:00:00.093

CustomerID CustomerAddress 1 82 Margate Drive, Sheffield, S4 8FQ 3 39 Queen Annes Drive, Bedale, DL8 2EL

In [19]:
-- 08. The change table returns four rows in total, one additional row for the DELETE.
-- NOTE: The __$operation column identifies the DML operation associated with the change. 1 = delete, 2 = insert, 3 = update (old values), 4 = update (new values).
SELECT * FROM cdc.dbo_Customer_CT;

(4 rows affected)

Total execution time: 00:00:00.090

__$start_lsn __$end_lsn __$seqval __$operation __$update_mask CustomerID CustomerAddress __$command_id 0x0000004200001BE800CD NULL 0x0000004200001BE800CA 2 0x03 1 82 Margate Drive, Sheffield, S4 8FQ 1 0x0000004200001BE800CD NULL 0x0000004200001BE800CB 2 0x03 2 135 High Barns, Ely, CB7 4RH 2 0x0000004200001BE800CD NULL 0x0000004200001BE800CC 2 0x03 3 39 Queen Annes Drive, Bedale, DL8 2EL 3 0x0000004200001E780007 NULL 0x0000004200001E780004 1 0x03 2 135 High Barns, Ely, CB7 4RH 1

In [20]:
-- 09. Update a row from the Customer table (UPDATE)
UPDATE dbo.Customer SET CustomerAddress = 'Guyzance Cottage, Guyzance NE65 9AF' WHERE CustomerID = 3;
SELECT * FROM dbo.Customer;

(1 row affected)

(2 rows affected)

Total execution time: 00:00:00.105

CustomerID CustomerAddress 1 82 Margate Drive, Sheffield, S4 8FQ 3 Guyzance Cottage, Guyzance NE65 9AF

In [25]:
-- 10. The change table returns six rows in total, two additional rows for the UPDATE (one for the old, one for the new).
-- NOTE: The __$operation column identifies the DML operation associated with the change. 1 = delete, 2 = insert, 3 = update (old values), 4 = update (new values).
SELECT * FROM cdc.dbo_Customer_CT;

(6 rows affected)

Total execution time: 00:00:00.086

__$start_lsn __$end_lsn __$seqval __$operation __$update_mask CustomerID CustomerAddress __$command_id 0x0000004200001BE800CD NULL 0x0000004200001BE800CA 2 0x03 1 82 Margate Drive, Sheffield, S4 8FQ 1 0x0000004200001BE800CD NULL 0x0000004200001BE800CB 2 0x03 2 135 High Barns, Ely, CB7 4RH 2 0x0000004200001BE800CD NULL 0x0000004200001BE800CC 2 0x03 3 39 Queen Annes Drive, Bedale, DL8 2EL 3 0x0000004200001E780007 NULL 0x0000004200001E780004 1 0x03 2 135 High Barns, Ely, CB7 4RH 1 0x0000004200001F380007 NULL 0x0000004200001F380006 3 0x02 3 39 Queen Annes Drive, Bedale, DL8 2EL 1 0x0000004200001F380007 NULL 0x0000004200001F380006 4 0x02 3 Guyzance Cottage, Guyzance NE65 9AF 1

## Query Changes

In [24]:
-- 11. It is recommended that you do not query the system tables (e.g. cdc.<capture instance>_CT) directly. 
-- Function: cdc.fn_cdc_get_all_changes_<capture_instance>
-- Description: Returns one row for each change applied to the source table within the specified log sequence number (LSN) range.
DECLARE @from_lsn binary(10), @to_lsn binary(10);  
SET @from_lsn = sys.fn_cdc_get_min_lsn('dbo_Customer');  
SET @to_lsn   = sys.fn_cdc_get_max_lsn();  
SELECT * FROM cdc.fn_cdc_get_all_changes_dbo_Customer (@from_lsn, @to_lsn, N'all');

(5 rows affected)

Total execution time: 00:00:00.138

__$start_lsn __$seqval __$operation __$update_mask CustomerID CustomerAddress 0x0000004200001BE800CD 0x0000004200001BE800CA 2 0x03 1 82 Margate Drive, Sheffield, S4 8FQ 0x0000004200001BE800CD 0x0000004200001BE800CB 2 0x03 2 135 High Barns, Ely, CB7 4RH 0x0000004200001BE800CD 0x0000004200001BE800CC 2 0x03 3 39 Queen Annes Drive, Bedale, DL8 2EL 0x0000004200001E780007 0x0000004200001E780004 1 0x03 2 135 High Barns, Ely, CB7 4RH 0x0000004200001F380007 0x0000004200001F380006 4 0x02 3 Guyzance Cottage, Guyzance NE65 9AF

In [26]:
-- 12. The following function will only be available if @supports_net_changes was activated when enabling the table for CDC (sys.sp_cdc_enable_table)
-- Function: cdc.fn_cdc_get_net_changes_<capture_instance>
-- Description: Returns one net change row for each source row changed within the specified Log Sequence Numbers (LSN) range.
DECLARE @begin_time datetime, @end_time datetime, @from_lsn binary(10), @to_lsn binary(10); 
SET @begin_time = DATEADD(day, -1, GETDATE());
SET @end_time = GETDATE();
SET @from_lsn = sys.fn_cdc_map_time_to_lsn('smallest greater than or equal', @begin_time);  
SET @to_lsn = sys.fn_cdc_map_time_to_lsn('largest less than or equal', @end_time);  
SELECT * FROM cdc.fn_cdc_get_net_changes_dbo_Customer(@from_lsn, @to_lsn, 'all');  
 

(2 rows affected)

Total execution time: 00:00:00.162

__$start_lsn __$operation __$update_mask CustomerID CustomerAddress 0x0000004200001BE800CD 2 NULL 1 82 Margate Drive, Sheffield, S4 8FQ 0x0000004200001F380007 2 NULL 3 Guyzance Cottage, Guyzance NE65 9AF

## Disable CDC

In [ ]:
-- 13. Disables change data capture for the specified source table and capture instance in the current database
sys.sp_cdc_disable_table
    @source_schema = N'dbo',   
    @source_name = N'Customer',  
    @capture_instance = N'dbo_Customer';

In [ ]:
-- 14. Disables change data capture for the current database
sys.sp_cdc_disable_db;

In [ ]:
-- 15. Drop Customer table if it exists
DROP TABLE IF EXISTS dbo.Customer;